## Expr
Converting strings into expressions.  Used in logic.py, planning.py and elsewhere.

In [2]:
from utils import *

In [3]:
x = expr('A | B')
x

(A | B)

In [4]:
type(x)

utils.Expr

In [5]:
x.op

'|'

In [6]:
x.args

(A, B)

In [7]:
w = expr('A <== B')
y = expr('A ==> B')
z = expr('A <=> B')
w, y, z

((A <== B), (A ==> B), (A <=> B))

In [9]:
x1 = expr('(A | B) ==> ~(C & D)')
x1

((A | B) ==> ~(C & D))

Expr is a recursive data structure.

In [10]:
x1.op

'==>'

In [11]:
x1.args

((A | B), ~(C & D))

In [10]:
type(x1.args[0])

utils.Expr

In [11]:
x1.args[0].op

'|'

# expr can also be used for arithmetic expressions

In [12]:
[expr('a + b ** c / d'), expr('x - sin(y) * e**x')]

[(a + ((b ** c) / d)), (x - (sin(y) * (e ** x)))]

This is useful if you are implementing computer algebra systems that perform symbolic mathematics.

## PropKB and logic.py 
We are going to focus on expr objects that represent propositional and first order logic (FOL) expressions.

In [12]:
from logic import *

We will create an instance of knowledge base for propositional logic.

In [13]:
kb = PropKB()

We add the above propositions to the knowledge base, as clauses.

In [14]:
kb.tell(x)
kb.tell(y)
kb.tell(z)
kb.tell(w)
kb.tell(x1)

In [15]:
kb.clauses

[x, y, z, (A | ~B), (~A | ~C | ~D), (~B | ~C | ~D)]

Note that the various ==>, <==, and <=> expressions were converts to disjunctive forms, using the or operator: |.  That is to make it easier to perform inference.

## Rules of inference: Modus Ponens

In [16]:
ikb = PropKB()
ikb.tell('A ==> B')
ikb.tell('A')

In [17]:
ikb.clauses

[(B | ~A), A]

In [19]:
ikb.ask(expr('B'))

{}

kb.tell() adds a clause to the KB.  kb.ask() queries the KB to see if the given clause can be deduced.  If the deduction is valid, ask() returns the binding list required to make it true.  An empty dictionary, {}, indicates (somewhat obscurely) that no substitution is required.  We can avoid this possible confusion by using ask_if_true()

In [20]:
ikb.ask_if_true(expr('B'))

True

In [21]:
ikb.ask(expr('C'))

False

In [22]:
ikb.ask_if_true(expr('C'))

False

In [23]:
ikb.clauses

[(B | ~A), A]

Note that even though ikb deduced that 'B' is valid, it did not add it to the knowledge base.

## And elimination

Fixed errors in expr: changed ^ to &

In [24]:
ikb.tell(expr('D & E'))

In [25]:
ikb.clauses

[(B | ~A), A, D, E]

In [26]:
ikb.ask(expr('E'))

{}

It looks like and elimination  works now.  Let's try and introduction.  We first retract the D & E clause.

In [27]:
ikb.retract(expr('D & E'))
ikb.clauses

[(B | ~A), A]

In [28]:
ikb.tell(expr('C'))
ikb.tell(expr('D'))

In [29]:
ikb.clauses

[(B | ~A), A, C, D]

In [30]:
ikb.ask(expr('C & D'))

{}

Good  Now we try or introduction.

In [32]:
ikb.ask_if_true(expr('C | B'))

True

In [33]:
ikb.ask(expr('D | E'))

{}

Eureka!  That works!  Now we try doublenegation elimination.

In [34]:
ikb.clauses

[(B | ~A), A, C, D]

In [35]:
ikb.tell(expr('~~E'))

In [36]:
ikb.clauses

[(B | ~A), A, C, D, E]

It looks like that happened automagically!

## Unit Resolution

In [35]:
ikb.clauses

[(B | ~A), A, C, D, E]

In [37]:
ikb.tell(expr('F | G'))

In [38]:
ikb.clauses

[(B | ~A), A, C, D, E, (F | G)]

In [39]:
ikb.tell(expr('~G'))

In [39]:
ikb.clauses

[(B | ~A), A, C, D, E, (F | G), ~G]

In [40]:
ikb.ask(expr('F'))

{}

## Resolution

In [41]:
ikb.clauses

[(B | ~A), A, C, D, E, (F | G), ~G]

In [42]:
ikb.tell(expr('H | I'))
ikb.tell(expr('~I | J'))

In [43]:
ikb.clauses

[(B | ~A), A, C, D, E, (F | G), ~G, (H | I), (~I | J)]

In [44]:
ikb.ask(expr('H | J'))

{}

Success!  This is how resolution works!

## Implication is transitive

In [45]:
ikb.tell('K ==> L')
ikb.tell('L ==> M')

In [46]:
ikb.clauses

[(B | ~A), A, C, D, E, (F | G), ~G, (H | I), (~I | J), (L | ~K), (M | ~L)]

In [47]:
ikb.ask(expr('K ==> M'))

{}

This works!